# Getting Started with Multiple MonoDAQs 

Here we represent how to fetch samples synchronously from two MonoDAQs one operating at 1 kSa/s and the other at 2 kSa/s.

In [1]:
from isotel.idm import monodaq, signal

## Attach the 1st MonoDAQ-U-X

We may randomly pick one, or we may provide a `name` parameter with it's serial number to always stick at the same one. To be able to distinguish the pin names from the other ones, we assign a prefix to be used in output streams signal names.

In [2]:
mdu1 = monodaq.MonoDAQ_U(prefix='A')
mdu1.print_setup()

## Attach the 2nd MonoDAQ-U-X

Exactly the same procedure as above, just that we assign to it a different prefix.

In [3]:
mdu2 = monodaq.MonoDAQ_U(exclude=[mdu1], prefix='B')
mdu2.print_setup()

## Create a Group

With the helper class `MonoDAQs_U()` one may combine any number of MonoDAQ-U-X which come from the same USB source and were successfully synchronized.

In [4]:
mdus = monodaq.MonoDAQs_U(mdu1, mdu2)

## Fetch Samples

The use of a group `fetch()` is exactly the same as `fetch()` for individual device. The output stream uses assigned prefixes to distinguish channels among devices.

In multi-rate environment the number of samples requested is equal to number of samples of the fastest stream, and others are terminated at that point. Here you may see `BV1` has 5 samples, while `AV1` obtained 3 samples.

In [5]:
list(signal.stream2signal(mdus.fetch(5)))

[{'AV1+ [V]': {'x': [0.0, 0.001, 0.002], 'y': [0.008, 0.005, 0.0065]},
  'BV1+ [V]': {'x': [0.0, 0.0005, 0.001, 0.0015, 0.002],
   'y': [0.054, 0.0525, 0.053, 0.053, 0.053]}}]

## Multi-Rate Math with Scope

You may observe `AV1+` is running at a lower rate (1 kSa/s) than `BV1+` (2 kSa/s), however math operations will still work well on concurrent samples as seen in this Scope example.

In this example we amplify the difference between the channels by 1000, where both MonoDAQs have left pins open.

In [6]:
N = 20000

signal.scope( 
    signal.stream2signal( 
        signal.addmath( mdus.fetch(N), 'diff [mV]', expr='1000*(AV1-BV1)'),
        split=500)
);

Loading BokehJS ...